<a href="https://colab.research.google.com/github/alezz0069/datasharing/blob/master/Api_test.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd

# Replace 'csv_link' with the URL link of your CSV file
csv_link = 'https://drive.google.com/uc?id=1lE-1EOlN0UaqO2xGRXWNt4MICm2uZg0j&export=download'

# Read the CSV file from the public link
df = pd.read_csv(csv_link)

# Display the DataFrame
df

datetime  machineID        volt      rotate    pressure  \
0       2015-01-01 06:00:00          1  176.217853  418.504078  113.077935   
1       2015-01-01 07:00:00          1  162.879223  402.747490   95.460525   
2       2015-01-01 08:00:00          1  170.989902  527.349825   75.237905   
3       2015-01-01 09:00:00          1  162.462833  346.149335  109.248561   
4       2015-01-01 10:00:00          1  157.610021  435.376873  111.886648   
...                     ...        ...         ...         ...         ...   
876095  2016-01-01 02:00:00        100  179.438162  395.222827  102.290715   
876096  2016-01-01 03:00:00        100  189.617555  446.207972   98.180607   
876097  2016-01-01 04:00:00        100  192.483414  447.816524   94.132837   
876098  2016-01-01 05:00:00        100  165.475310  413.771670  104.081073   
876099  2016-01-01 06:00:00        100  171.336037  496.096870   79.095538   

        vibration  
0       45.087686  
1       43.413973  
2       34.178847  
3       41.122144  
4       25.990511  
...           ...  
876095  50.771941  
876096  35.123072  
876097  48.314561  
876098  44.835259  
876099  37.845245  

[876100 rows x 6 columns]

In [ ]:
import requests
import pandas as pd
from datetime import datetime
import time

In [ ]:
import pandas as pd
import requests
import time

# Sample DataFrame
data = {
    'datetime': ['2023-05-18 10:00:00', '2023-05-18 10:05:00', '2023-05-18 10:10:00'],
    'machineID': [1, 2, 3],
    'volt': [170, 190, 155],
    'rotate': [400, 500, 380],
    'pressure': [90, 110, 100],
    'vibration': [30, 50, 25]
}
df_scada = pd.DataFrame(data)

# API endpoint URL
api_url = 'http://alezzdog2.pythonanywhere.com'

# Function to call the API for a single row
def call_api(row):
    # Extract the required data from the row
    datetime_value = row['datetime']
    machineID = row['machineID']
    volt = row['volt']
    rotate = row['rotate']
    pressure = row['pressure']
    vibration = row['vibration']

    # Prepare the data to be sent to the API
    payload = {
        'datetime': datetime_value,
        'machineID': machineID,
        'volt': volt,
        'rotate': rotate,
        'pressure': pressure,
        'vibration': vibration
    }

    # Send a POST request to the API
    response = requests.post(api_url, json=payload)

    # Get the API response as text
    api_output = response.text

    # Return the API output
    return api_output

# Continuously read and process rows from df_scada
while True:
    for index, row in df_scada.iterrows():
        # Call the API for the current row
        output = call_api(row)
        
        # Print the API output
        print(output)

        # Delay of 5 seconds before processing the next row
        time.sleep(5)


Sensor data at 2023-05-19 12:25:14:
Machine ID: 1
Voltage: 170 (Nominal value)
Rotation: 400 (Below the 25th percentile)
Pressure: 90 (Below the 25th percentile)
Vibration: 30 (Below the 25th percentile)
Sensor data at 2023-05-19 12:25:19:
Machine ID: 2
Voltage: 190 (Above the 75th percentile)
Rotation: 500 (Above the 75th percentile)
Pressure: 110 (Above the 75th percentile)
Vibration: 50 (Above the 75th percentile)


KeyboardInterrupt: ignored

In [ ]:
# Import the required libraries
import pandas as pd
import requests
import time

# Function to call the API for a single row
def call_api(row):
    # Extract the required data from the row
    datetime_value = row['datetime']
    machineID = row['machineID']
    volt = row['volt']
    rotate = row['rotate']
    pressure = row['pressure']
    vibration = row['vibration']

    # Construct the API endpoint URL
    api_url = 'http://alezzdog2.pythonanywhere.com'

    # Prepare the data to be sent to the API
    payload = {
        'datetime': datetime_value,
        'machineID': machineID,
        'volt': volt,
        'rotate': rotate,
        'pressure': pressure,
        'vibration': vibration
    }

    # Send a POST request to the API
    response = requests.post(api_url, json=payload)

    # Get the API response as text
    api_output = response.text

    # Return the API output
    return api_output

# Create a sample DataFrame
data = df.copy()
df_scada = pd.DataFrame(data)

# Create a new DataFrame to accumulate inputs and outputs
df_accumulated = pd.DataFrame(columns=['datetime', 'machineID', 'volt', 'rotate', 'pressure', 'vibration', 'output'])
consecutive_count = {sensor: 0 for sensor in ['volt', 'rotate', 'pressure', 'vibration']}
failure_threshold = 8
machine_failure_threshold = 12

# Set display options for printing the DataFrame
pd.set_option('display.expand_frame_repr', False)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Continuously read and process rows from df_scada
while True:
    for index, row in df_scada.iterrows():
        # Call the API for the current row
        output = call_api(row)

        # Add the row and API output to the accumulated DataFrame
        row['output'] = output
        df_accumulated = pd.concat([df_accumulated, row.to_frame().T], ignore_index=True)
        df_accumulated['datetime'] = df['datetime']  # Update datetime column with original values
        display(df_accumulated)

        # Check for consecutive failures
        for sensor in ['volt', 'rotate', 'pressure', 'vibration']:
            sensor_value = df_accumulated.at[df_accumulated.index[-1], sensor]
            if isinstance(sensor_value, float):
                threshold_high = globals()[f"{sensor}_q75"]
                threshold_low = globals()[f"{sensor}_q25"]
                if sensor_value > threshold_high or sensor_value < threshold_low:
                    consecutive_count[sensor] += 1
                    if consecutive_count[sensor] >= failure_threshold:
                        df_accumulated.at[df_accumulated.index[-1], 'output'] = f'Imminent failure in {sensor} sensor'
                        if consecutive_count[sensor] >= machine_failure_threshold:
                            df_accumulated.at[df_accumulated.index[-1], 'output'] = '⚠️ Machine Failure'
                else:
                    consecutive_count[sensor] = 0

        # Delay of 5 seconds before processing the next row
        time.sleep(0.2)



datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3  2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3  2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...
4  2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 13:18:01:\nMachine I...

...

datetime machineID        volt      rotate    pressure  vibration                                             output
0    2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1    2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2    2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3    2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...
4    2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 13:18:01:\nMachine I...
5    2015-01-01 11:00:00         1  172.504839  430.323362   95.927042  35.655017  Sensor data at 2023-05-19 13:18:01:\nMachine I...
6    2015-01-01 12:00:00         1  156.556031  499.071623  111.755684   42.75392  Sensor data at 2023-05-19 13:18:01:\nMachine I...
7    2015-01-01 13:00:00         1  172.522781  409.624717  101.001083  35.482009  Sensor data at 2023-05-19 13:18:01:\nMachine I...
8    2015-01-01 14:00:00         1  175.324524  398.648781  110.624361  45.482287  Sensor data at 2023-05-19 13:18:02:\nMachine I...
9    2015-01-01 15:00:00         1  169.218423   460.85067   104.84823  39.901735  Sensor data at 2023-05-19 13:18:02:\nMachine I...
10   2015-01-01 16:00:00         1  167.060981  382.483543  103.780663    42.6758  Sensor data at 2023-05-19 13:18:02:\nMachine I...
11   2015-01-01 17:00:00         1  160.263954  448.084256   96.480976  38.543681  Sensor data at 2023-05-19 13:18:02:\nMachine I...
12   2015-01-01 18:00:00         1  153.353492  490.672921    86.01244  44.108554  Sensor data at 2023-05-19 13:18:03:\nMachine I...
13   2015-01-01 19:00:00         1  182.739113  418.199252   93.484954   41.36719  Sensor data at 2023-05-19 13:18:03:\nMachine I...
14   2015-01-01 20:00:00         1  170.335438  402.461187   93.235787  39.739883  Sensor data at 2023-05-19 13:18:03:\nMachine I...
15   2015-01-01 21:00:00         1  182.467109  501.918973   85.762615  51.021486  Sensor data at 2023-05-19 13:18:03:\nMachine I...
16   2015-01-01 22:00:00         1  151.335682  444.922656   94.247371  42.119652  Sensor data at 2023-05-19 13:18:03:\nMachine I...
17   2015-01-01 23:00:00         1  172.535396  511.886364   91.329429  32.248832  Sensor data at 2023-05-19 13:18:04:\nMachine I...
18   2015-01-02 00:00:00         1  180.097495  486.712304   96.733915  38.896776  Sensor data at 2023-05-19 13:18:04:\nMachine I...
19   2015-01-02 01:00:00         1  169.605854  519.452812    78.88078  40.156875  Sensor data at 2023-05-19 13:18:04:\nMachine I...
20   2015-01-02 02:00:00         1  167.129117  427.050768   91.699899  44.642351  Sensor data at 2023-05-19 13:18:04:\nMachine I...
21   2015-01-02 03:00:00         1    158.2714  422.811052   92.439132  39.781917  Sensor data at 2023-05-19 13:18:05:\nMachine I...
22   2015-01-02 04:00:00         1   200.87243  403.235951   96.535487  32.516838  Sensor data at 2023-05-19 13:18:05:\nMachine I...
23   2015-01-02 05:00:00         1  181.257522  495.777958    93.43929  52.355876  Sensor data at 2023-05-19 13:18:05:\nMachine I...
24   2015-01-02 06:00:00         1  197.363125  446.943947  114.342061  29.527665  Sensor data at 2023-05-19 13:18:05:\nMachine I...
25   2015-01-02 07:00:00         1  171.200895  384.645962  103.373293  35.796566  Sensor data at 2023-05-19 13:18:05:\nMachine I...
26   2015-01-02 08:00:00         1  160.528861  486.459056   86.944273  42.992509  Sensor data at 2023-05-19 13:18:06:\nMachine I...
27   2015-01-02 09:00:00         1  147.300678  420.610792  110.408985  34.203042  Sensor data at 2023-05-19 13:18:06:\nMachine I...
28   2015-01-02 10:00:00         1  160.458503  412.965696   90.711354  36.963766  Sensor data at 2023-05-19 13:18:06:\nMachine I...
29   2015-01-02 11:00:00  

datetime machineID        volt      rotate    pressure  vibration                                             output
0    2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1    2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2    2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3    2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...
4    2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 13:18:01:\nMachine I...
5    2015-01-01 11:00:00         1  172.504839  430.323362   95.927042  35.655017  Sensor data at 2023-05-19 13:18:01:\nMachine I...
6    2015-01-01 12:00:00         1  156.556031  499.071623  111.755684   42.75392  Sensor data at 2023-05-19 13:18:01:\nMachine I...
7    2015-01-01 13:00:00         1  172.522781  409.624717  101.001083  35.482009  Sensor data at 2023-05-19 13:18:01:\nMachine I...
8    2015-01-01 14:00:00         1  175.324524  398.648781  110.624361  45.482287  Sensor data at 2023-05-19 13:18:02:\nMachine I...
9    2015-01-01 15:00:00         1  169.218423   460.85067   104.84823  39.901735  Sensor data at 2023-05-19 13:18:02:\nMachine I...
10   2015-01-01 16:00:00         1  167.060981  382.483543  103.780663    42.6758  Sensor data at 2023-05-19 13:18:02:\nMachine I...
11   2015-01-01 17:00:00         1  160.263954  448.084256   96.480976  38.543681  Sensor data at 2023-05-19 13:18:02:\nMachine I...
12   2015-01-01 18:00:00         1  153.353492  490.672921    86.01244  44.108554  Sensor data at 2023-05-19 13:18:03:\nMachine I...
13   2015-01-01 19:00:00         1  182.739113  418.199252   93.484954   41.36719  Sensor data at 2023-05-19 13:18:03:\nMachine I...
14   2015-01-01 20:00:00         1  170.335438  402.461187   93.235787  39.739883  Sensor data at 2023-05-19 13:18:03:\nMachine I...
15   2015-01-01 21:00:00         1  182.467109  501.918973   85.762615  51.021486  Sensor data at 2023-05-19 13:18:03:\nMachine I...
16   2015-01-01 22:00:00         1  151.335682  444.922656   94.247371  42.119652  Sensor data at 2023-05-19 13:18:03:\nMachine I...
17   2015-01-01 23:00:00         1  172.535396  511.886364   91.329429  32.248832  Sensor data at 2023-05-19 13:18:04:\nMachine I...
18   2015-01-02 00:00:00         1  180.097495  486.712304   96.733915  38.896776  Sensor data at 2023-05-19 13:18:04:\nMachine I...
19   2015-01-02 01:00:00         1  169.605854  519.452812    78.88078  40.156875  Sensor data at 2023-05-19 13:18:04:\nMachine I...
20   2015-01-02 02:00:00         1  167.129117  427.050768   91.699899  44.642351  Sensor data at 2023-05-19 13:18:04:\nMachine I...
21   2015-01-02 03:00:00         1    158.2714  422.811052   92.439132  39.781917  Sensor data at 2023-05-19 13:18:05:\nMachine I...
22   2015-01-02 04:00:00         1   200.87243  403.235951   96.535487  32.516838  Sensor data at 2023-05-19 13:18:05:\nMachine I...
23   2015-01-02 05:00:00         1  181.257522  495.777958    93.43929  52.355876  Sensor data at 2023-05-19 13:18:05:\nMachine I...
24   2015-01-02 06:00:00         1  197.363125  446.943947  114.342061  29.527665  Sensor data at 2023-05-19 13:18:05:\nMachine I...
25   2015-01-02 07:00:00         1  171.200895  384.645962  103.373293  35.796566  Sensor data at 2023-05-19 13:18:05:\nMachine I...
26   2015-01-02 08:00:00         1  160.528861  486.459056   86.944273  42.992509  Sensor data at 2023-05-19 13:18:06:\nMachine I...
27   2015-01-02 09:00:00         1  147.300678  420.610792  110.408985  34.203042  Sensor data at 2023-05-19 13:18:06:\nMachine I...
28   2015-01-02 10:00:00         1  160.458503  412.965696   90.711354  36.963766  Sensor data at 2023-05-19 13:18:06:\nMachine I...
29   2015-01-02 11:00:00  

datetime machineID        volt      rotate    pressure  vibration                                             output
0    2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1    2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2    2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3    2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...
4    2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 13:18:01:\nMachine I...
5    2015-01-01 11:00:00         1  172.504839  430.323362   95.927042  35.655017  Sensor data at 2023-05-19 13:18:01:\nMachine I...
6    2015-01-01 12:00:00         1  156.556031  499.071623  111.755684   42.75392  Sensor data at 2023-05-19 13:18:01:\nMachine I...
7    2015-01-01 13:00:00         1  172.522781  409.624717  101.001083  35.482009  Sensor data at 2023-05-19 13:18:01:\nMachine I...
8    2015-01-01 14:00:00         1  175.324524  398.648781  110.624361  45.482287  Sensor data at 2023-05-19 13:18:02:\nMachine I...
9    2015-01-01 15:00:00         1  169.218423   460.85067   104.84823  39.901735  Sensor data at 2023-05-19 13:18:02:\nMachine I...
10   2015-01-01 16:00:00         1  167.060981  382.483543  103.780663    42.6758  Sensor data at 2023-05-19 13:18:02:\nMachine I...
11   2015-01-01 17:00:00         1  160.263954  448.084256   96.480976  38.543681  Sensor data at 2023-05-19 13:18:02:\nMachine I...
12   2015-01-01 18:00:00         1  153.353492  490.672921    86.01244  44.108554  Sensor data at 2023-05-19 13:18:03:\nMachine I...
13   2015-01-01 19:00:00         1  182.739113  418.199252   93.484954   41.36719  Sensor data at 2023-05-19 13:18:03:\nMachine I...
14   2015-01-01 20:00:00         1  170.335438  402.461187   93.235787  39.739883  Sensor data at 2023-05-19 13:18:03:\nMachine I...
15   2015-01-01 21:00:00         1  182.467109  501.918973   85.762615  51.021486  Sensor data at 2023-05-19 13:18:03:\nMachine I...
16   2015-01-01 22:00:00         1  151.335682  444.922656   94.247371  42.119652  Sensor data at 2023-05-19 13:18:03:\nMachine I...
17   2015-01-01 23:00:00         1  172.535396  511.886364   91.329429  32.248832  Sensor data at 2023-05-19 13:18:04:\nMachine I...
18   2015-01-02 00:00:00         1  180.097495  486.712304   96.733915  38.896776  Sensor data at 2023-05-19 13:18:04:\nMachine I...
19   2015-01-02 01:00:00         1  169.605854  519.452812    78.88078  40.156875  Sensor data at 2023-05-19 13:18:04:\nMachine I...
20   2015-01-02 02:00:00         1  167.129117  427.050768   91.699899  44.642351  Sensor data at 2023-05-19 13:18:04:\nMachine I...
21   2015-01-02 03:00:00         1    158.2714  422.811052   92.439132  39.781917  Sensor data at 2023-05-19 13:18:05:\nMachine I...
22   2015-01-02 04:00:00         1   200.87243  403.235951   96.535487  32.516838  Sensor data at 2023-05-19 13:18:05:\nMachine I...
23   2015-01-02 05:00:00         1  181.257522  495.777958    93.43929  52.355876  Sensor data at 2023-05-19 13:18:05:\nMachine I...
24   2015-01-02 06:00:00         1  197.363125  446.943947  114.342061  29.527665  Sensor data at 2023-05-19 13:18:05:\nMachine I...
25   2015-01-02 07:00:00         1  171.200895  384.645962  103.373293  35.796566  Sensor data at 2023-05-19 13:18:05:\nMachine I...
26   2015-01-02 08:00:00         1  160.528861  486.459056   86.944273  42.992509  Sensor data at 2023-05-19 13:18:06:\nMachine I...
27   2015-01-02 09:00:00         1  147.300678  420.610792  110.408985  34.203042  Sensor data at 2023-05-19 13:18:06:\nMachine I...
28   2015-01-02 10:00:00         1  160.458503  412.965696   90.711354  36.963766  Sensor data at 2023-05-19 13:18:06:\nMachine I...
29   2015-01-02 11:00:00  

datetime machineID        volt      rotate    pressure  vibration                                             output
0    2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1    2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2    2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3    2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...
4    2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 13:18:01:\nMachine I...
5    2015-01-01 11:00:00         1  172.504839  430.323362   95.927042  35.655017  Sensor data at 2023-05-19 13:18:01:\nMachine I...
6    2015-01-01 12:00:00         1  156.556031  499.071623  111.755684   42.75392  Sensor data at 2023-05-19 13:18:01:\nMachine I...
7    2015-01-01 13:00:00         1  172.522781  409.624717  101.001083  35.482009  Sensor data at 2023-05-19 13:18:01:\nMachine I...
8    2015-01-01 14:00:00         1  175.324524  398.648781  110.624361  45.482287  Sensor data at 2023-05-19 13:18:02:\nMachine I...
9    2015-01-01 15:00:00         1  169.218423   460.85067   104.84823  39.901735  Sensor data at 2023-05-19 13:18:02:\nMachine I...
10   2015-01-01 16:00:00         1  167.060981  382.483543  103.780663    42.6758  Sensor data at 2023-05-19 13:18:02:\nMachine I...
11   2015-01-01 17:00:00         1  160.263954  448.084256   96.480976  38.543681  Sensor data at 2023-05-19 13:18:02:\nMachine I...
12   2015-01-01 18:00:00         1  153.353492  490.672921    86.01244  44.108554  Sensor data at 2023-05-19 13:18:03:\nMachine I...
13   2015-01-01 19:00:00         1  182.739113  418.199252   93.484954   41.36719  Sensor data at 2023-05-19 13:18:03:\nMachine I...
14   2015-01-01 20:00:00         1  170.335438  402.461187   93.235787  39.739883  Sensor data at 2023-05-19 13:18:03:\nMachine I...
15   2015-01-01 21:00:00         1  182.467109  501.918973   85.762615  51.021486  Sensor data at 2023-05-19 13:18:03:\nMachine I...
16   2015-01-01 22:00:00         1  151.335682  444.922656   94.247371  42.119652  Sensor data at 2023-05-19 13:18:03:\nMachine I...
17   2015-01-01 23:00:00         1  172.535396  511.886364   91.329429  32.248832  Sensor data at 2023-05-19 13:18:04:\nMachine I...
18   2015-01-02 00:00:00         1  180.097495  486.712304   96.733915  38.896776  Sensor data at 2023-05-19 13:18:04:\nMachine I...
19   2015-01-02 01:00:00         1  169.605854  519.452812    78.88078  40.156875  Sensor data at 2023-05-19 13:18:04:\nMachine I...
20   2015-01-02 02:00:00         1  167.129117  427.050768   91.699899  44.642351  Sensor data at 2023-05-19 13:18:04:\nMachine I...
21   2015-01-02 03:00:00         1    158.2714  422.811052   92.439132  39.781917  Sensor data at 2023-05-19 13:18:05:\nMachine I...
22   2015-01-02 04:00:00         1   200.87243  403.235951   96.535487  32.516838  Sensor data at 2023-05-19 13:18:05:\nMachine I...
23   2015-01-02 05:00:00         1  181.257522  495.777958    93.43929  52.355876  Sensor data at 2023-05-19 13:18:05:\nMachine I...
24   2015-01-02 06:00:00         1  197.363125  446.943947  114.342061  29.527665  Sensor data at 2023-05-19 13:18:05:\nMachine I...
25   2015-01-02 07:00:00         1  171.200895  384.645962  103.373293  35.796566  Sensor data at 2023-05-19 13:18:05:\nMachine I...
26   2015-01-02 08:00:00         1  160.528861  486.459056   86.944273  42.992509  Sensor data at 2023-05-19 13:18:06:\nMachine I...
27   2015-01-02 09:00:00         1  147.300678  420.610792  110.408985  34.203042  Sensor data at 2023-05-19 13:18:06:\nMachine I...
28   2015-01-02 10:00:00         1  160.458503  412.965696   90.711354  36.963766  Sensor data at 2023-05-19 13:18:06:\nMachine I...
29   2015-01-02 11:00:00  

KeyboardInterrupt: ignored

In [ ]:
df_accumulated

datetime machineID        volt      rotate    pressure  vibration                                             output
0    2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 13:18:00:\nMachine I...
1    2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 13:18:00:\nMachine I...
2    2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 13:18:00:\nMachine I...
3    2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 13:18:01:\nMachine I...
4    2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 13:18:01:\nMachine I...
5    2015-01-01 11:00:00         1  172.504839  430.323362   95.927042  35.655017  Sensor data at 2023-05-19 13:18:01:\nMachine I...
6    2015-01-01 12:00:00         1  156.556031  499.071623  111.755684   42.75392  Sensor data at 2023-05-19 13:18:01:\nMachine I...
7    2015-01-01 13:00:00         1  172.522781  409.624717  101.001083  35.482009  Sensor data at 2023-05-19 13:18:01:\nMachine I...
8    2015-01-01 14:00:00         1  175.324524  398.648781  110.624361  45.482287  Sensor data at 2023-05-19 13:18:02:\nMachine I...
9    2015-01-01 15:00:00         1  169.218423   460.85067   104.84823  39.901735  Sensor data at 2023-05-19 13:18:02:\nMachine I...
10   2015-01-01 16:00:00         1  167.060981  382.483543  103.780663    42.6758  Sensor data at 2023-05-19 13:18:02:\nMachine I...
11   2015-01-01 17:00:00         1  160.263954  448.084256   96.480976  38.543681  Sensor data at 2023-05-19 13:18:02:\nMachine I...
12   2015-01-01 18:00:00         1  153.353492  490.672921    86.01244  44.108554  Sensor data at 2023-05-19 13:18:03:\nMachine I...
13   2015-01-01 19:00:00         1  182.739113  418.199252   93.484954   41.36719  Sensor data at 2023-05-19 13:18:03:\nMachine I...
14   2015-01-01 20:00:00         1  170.335438  402.461187   93.235787  39.739883  Sensor data at 2023-05-19 13:18:03:\nMachine I...
15   2015-01-01 21:00:00         1  182.467109  501.918973   85.762615  51.021486  Sensor data at 2023-05-19 13:18:03:\nMachine I...
16   2015-01-01 22:00:00         1  151.335682  444.922656   94.247371  42.119652  Sensor data at 2023-05-19 13:18:03:\nMachine I...
17   2015-01-01 23:00:00         1  172.535396  511.886364   91.329429  32.248832  Sensor data at 2023-05-19 13:18:04:\nMachine I...
18   2015-01-02 00:00:00         1  180.097495  486.712304   96.733915  38.896776  Sensor data at 2023-05-19 13:18:04:\nMachine I...
19   2015-01-02 01:00:00         1  169.605854  519.452812    78.88078  40.156875  Sensor data at 2023-05-19 13:18:04:\nMachine I...
20   2015-01-02 02:00:00         1  167.129117  427.050768   91.699899  44.642351  Sensor data at 2023-05-19 13:18:04:\nMachine I...
21   2015-01-02 03:00:00         1    158.2714  422.811052   92.439132  39.781917  Sensor data at 2023-05-19 13:18:05:\nMachine I...
22   2015-01-02 04:00:00         1   200.87243  403.235951   96.535487  32.516838  Sensor data at 2023-05-19 13:18:05:\nMachine I...
23   2015-01-02 05:00:00         1  181.257522  495.777958    93.43929  52.355876  Sensor data at 2023-05-19 13:18:05:\nMachine I...
24   2015-01-02 06:00:00         1  197.363125  446.943947  114.342061  29.527665  Sensor data at 2023-05-19 13:18:05:\nMachine I...
25   2015-01-02 07:00:00         1  171.200895  384.645962  103.373293  35.796566  Sensor data at 2023-05-19 13:18:05:\nMachine I...
26   2015-01-02 08:00:00         1  160.528861  486.459056   86.944273  42.992509  Sensor data at 2023-05-19 13:18:06:\nMachine I...
27   2015-01-02 09:00:00         1  147.300678  420.610792  110.408985  34.203042  Sensor data at 2023-05-19 13:18:06:\nMachine I...
28   2015-01-02 10:00:00         1  160.458503  412.965696   90.711354  36.963766  Sensor data at 2023-05-19 13:18:06:\nMachine I...
29   2015-01-02 11:00:00  

In [ ]:
# Import the required libraries
import pandas as pd
import requests
import time

# Function to call the API for a single row
def call_api(row):
    # Extract the required data from the row
    datetime_value = row['datetime']
    machineID = row['machineID']
    volt = row['volt']
    rotate = row['rotate']
    pressure = row['pressure']
    vibration = row['vibration']

    # Construct the API endpoint URL
    api_url = 'http://alezzdog2.pythonanywhere.com'

    # Prepare the data to be sent to the API
    payload = {
        'datetime': datetime_value,
        'machineID': machineID,
        'volt': volt,
        'rotate': rotate,
        'pressure': pressure,
        'vibration': vibration
    }

    # Send a POST request to the API
    response = requests.post(api_url, json=payload)

    # Get the API response as text
    api_output = response.text

    # Return the API output
    return api_output

# Create a sample DataFrame
data = df.copy()
df_scada = pd.DataFrame(data)

# Create a new DataFrame to accumulate inputs and outputs
df_accumulated = pd.DataFrame(columns=['datetime', 'machineID', 'volt', 'rotate', 'pressure', 'vibration', 'output'])
consecutive_count = {sensor: 0 for sensor in ['volt', 'rotate', 'pressure', 'vibration']}
failure_threshold = 1

# Set display options for printing the DataFrame
pd.set_option('display.expand_frame_repr', False)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Continuously read and process rows from df_scada
while True:
    for index, row in df_scada.iterrows():
        # Call the API for the current row
        output = call_api(row)

        # Add the row and API output to the accumulated DataFrame
        row['output'] = output
        df_accumulated = pd.concat([df_accumulated, row.to_frame().T], ignore_index=True)
        df_accumulated['datetime'] = df['datetime']  # Update datetime column with original values
        display(df_accumulated)

        # Check for consecutive failures
        for sensor in ['volt', 'rotate', 'pressure', 'vibration']:
            if 'Above the 75th percentile' in df_accumulated[sensor].values[-failure_threshold:]:
                consecutive_count[sensor] += 1
            elif 'Below the 25th percentile' in df_accumulated[sensor].values[-failure_threshold:]:
                consecutive_count[sensor] += 1
            else:
                consecutive_count[sensor] = 0

            if consecutive_count[sensor] >= failure_threshold:
                print(f'Imminent failure in {sensor} sensor detected!')

        # Delay of 5 seconds before processing the next row
        time.sleep(5)


datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 12:38:12:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 12:38:12:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 12:38:17:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 12:38:12:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 12:38:17:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 12:38:22:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 12:38:12:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 12:38:17:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 12:38:22:\nMachine I...
3  2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 12:38:27:\nMachine I...

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 12:38:12:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 12:38:17:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 12:38:22:\nMachine I...
3  2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 12:38:27:\nMachine I...
4  2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 12:38:32:\nMachine I...

KeyboardInterrupt: ignored

In [ ]:
df_accumulated

datetime machineID        volt      rotate    pressure  vibration                                             output
0  2015-01-01 06:00:00         1  176.217853  418.504078  113.077935  45.087686  Sensor data at 2023-05-19 12:38:12:\nMachine I...
1  2015-01-01 07:00:00         1  162.879223   402.74749   95.460525  43.413973  Sensor data at 2023-05-19 12:38:17:\nMachine I...
2  2015-01-01 08:00:00         1  170.989902  527.349825   75.237905  34.178847  Sensor data at 2023-05-19 12:38:22:\nMachine I...
3  2015-01-01 09:00:00         1  162.462833  346.149335  109.248561  41.122144  Sensor data at 2023-05-19 12:38:27:\nMachine I...
4  2015-01-01 10:00:00         1  157.610021  435.376873  111.886648  25.990511  Sensor data at 2023-05-19 12:38:32:\nMachine I...

APi:

In [ ]:
from flask import Flask, request
from datetime import datetime

app = Flask(__name__)

# Define percentile thresholds
volt_q75 = 180.929341
rotate_q75 = 481.358342
pressure_q75 = 107.377475
vibration_q75 = 44.004311
volt_q25 = 160.382124
rotate_q25 = 412.348209
pressure_q25 = 93.320867
vibration_q25 = 36.847203

@app.route('/', methods=['POST'])
def process_sensor_data():
    # Receive the JSON payload containing sensor data
    sensor_data = request.json
    
    # Extract the sensor values from the payload
    machineID = sensor_data['machineID']
    volt = sensor_data['volt']
    rotate = sensor_data['rotate']
    pressure = sensor_data['pressure']
    vibration = sensor_data['vibration']

    # Determine the status for each sensor value
    status_volt = get_status(volt, volt_q25, volt_q75)
    status_rotate = get_status(rotate, rotate_q25, rotate_q75)
    status_pressure = get_status(pressure, pressure_q25, pressure_q75)
    status_vibration = get_status(vibration, vibration_q25, vibration_q75)

    # Get the current date and time
    current_datetime = datetime.now().strftime('%Y-%m-%d %H:%M:%S')

    # Create the response message
    response = f"Sensor data at {current_datetime}:\n" \
               f"Machine ID: {machineID}\n" \
               f"Voltage: {volt} ({status_volt})\n" \
               f"Rotation: {rotate} ({status_rotate})\n" \
               f"Pressure: {pressure} ({status_pressure})\n" \
               f"Vibration: {vibration} ({status_vibration})"

    return response

def get_status(value, q25, q75):
    if value > q75:
        return "Above the 75th percentile"
    elif value < q25:
        return "Below the 25th percentile"
    else:
        return "Nominal value"

if __name__ == '__main__':
    app.run(port=8080)


 * Serving Flask app '__main__'
 * Debug mode: off


Address already in use
Port 8080 is in use by another program. Either identify and stop that program, or start the server with a different port.
ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/werkzeug/serving.py", line 748, in __init__
    self.server_bind()
  File "/usr/lib/python3.10/http/server.py", line 137, in server_bind
    socketserver.TCPServer.server_bind(self)
  File "/usr/lib/python3.10/socketserver.py", line 466, in server_bind
    self.socket.bind(self.server_address)
OSError: [Errno 98] Address already in use

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-45-c9c2406be73b>", line 56, in <cell line: 55>
    app.run(port=8080)
  File "/usr/local/lib/python3.10/dist-packages/flask/app.py", line 1191, in run
    run_simple(t.cast(str, host), port, self, **options)
  File "/usr/local/lib/python3.10/dist-packages/werkzeug/serving.py", line 1075, in

TypeError: ignored